In [2]:
!pip install torch
!pip install transformers
!pip install datasets

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.2/7.2 MB 91.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 236.8/236.8 kB 26.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 111.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 73.7 MB/s eta 0:00:00
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 485.6/485.6 kB 18.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 15.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.5/212.5 kB 25.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.3/134.3 kB 16.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 32.

In [3]:
!git clone --single-branch git://gonito.net/challenging-america-word-gap-prediction -b master

Cloning into 'challenging-america-word-gap-prediction'...
remote: Wymienianie obiektów: 27, gotowe.
remote: Zliczanie obiektów: 100% (27/27), gotowe.
remote: Kompresowanie obiektów: 100% (23/23), gotowe.
remote: Razem 27 (delty 2), użyte ponownie 17 (delty 0), paczki użyte ponownie 0
Receiving objects: 100% (27/27), 278.33 MiB | 21.80 MiB/s, done.
Resolving deltas: 100% (2/2), done.


In [4]:
import torch
import sys
from transformers import GPT2Tokenizer, GPT2LMHeadModel


In [5]:
import torch
import sys
from transformers import GPT2Tokenizer, GPT2LMHeadModel

import lzma
from itertools import islice
import regex as re
import math
import sys
from torchtext.vocab import build_vocab_from_iterator
from torch import nn
from torch.utils.data import IterableDataset
import itertools

In [6]:
%cd /content/challenging-america-word-gap-prediction

/content/challenging-america-word-gap-prediction


In [7]:

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

In [8]:
tokenizer = GPT2Tokenizer.from_pretrained("gpt2-large")
model = GPT2LMHeadModel.from_pretrained("gpt2-large").to(device)

In [1]:
def create_outputs(folder_name):
    print(f'Creating outputs in {folder_name}')
    with lzma.open(f'{folder_name}/in.tsv.xz', mode='rt', encoding='utf-8') as fid:
        with open(f'{folder_name}/out-{folder_name}.tsv', 'w', encoding='utf-8', newline='\n') as f:
            for line in fid:
                separated = line.split('\t')
                prefix = separated[6].replace(r'\n', ' ')
                new_val = []
                for j in range(5):
                  val = 1
                  prefix = separated[6].replace(r'\n', ' ')
                  for i in range(5):
                    left_context =tokenizer.encode(prefix, return_tensors="pt").to(device)
                    out = model(left_context)
                    prob_dist=torch.softmax(out[0][0][-1],dim=0)
                    values,index  =prob_dist.topk(5)
                    token = []
                    total = 0
                    for x in index:
                      token.append(tokenizer.decode(x))
                    zipped = list(zip(values, token))
                    val *=float(values[0])
                    prefix+=' '+zipped[j][1].strip()
                  new_val.append(math.sqrt(val))
                prefix = separated[6].replace(r'\n', ' ')
                left_context =tokenizer.encode(prefix, return_tensors="pt").to(device)
                out = model(left_context)
                prob_dist=torch.softmax(out[0][0][-1],dim=0)
                values,index  =prob_dist.topk(5)
                token = []
                for x in index:
                  token.append(tokenizer.decode(x))
                output = new_val
                zipped = list(zip(output, token))
                res = sorted(zipped, key = lambda x: x[1])

                output_line = ' '.join([f'{x[1].strip()}:{x[0]}' for x in res])
                f.write(output_line + '\n')

In [9]:
create_outputs('dev-0')
create_outputs('test-A')

Creating outputs in dev-0
Creating outputs in test-A
